# 文本语义分析


## 0. 前期准备


### 0.1 安装相关库

此步仅需在新环境中运行


In [1]:
%pip install numpy<2
%pip install pandas
%pip install openpyxl
%pip install jieba
%pip install nltk
%pip install spacy
%pip install matplotlib

Note: you may need to restart the kernel to use updated packages.


ϵͳ�Ҳ���ָ�����ļ���


Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simple
Note: you may need to restart the kernel to use updated packages.
Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simple
Note: you may need to restart the kernel to use updated packages.
Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simple
Note: you may need to restart the kernel to use updated packages.
Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simple
Note: you may need to restart the kernel to use updated packages.
Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simpleNote: you may need to restart the kernel to use updated packages.

Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simple
Note: you may need to restart the kernel to use updated packages.


In [2]:
%pip install zh_core_web_sm-3.7.0-py3-none-any.whl

Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simple
Processing c:\users\sparr\desktop\text-analysis\zh_core_web_sm-3.7.0-py3-none-any.whl
zh-core-web-sm is already installed with the same version as the provided wheel. Use --force-reinstall to force an installation of the wheel.
Note: you may need to restart the kernel to use updated packages.


### 0.2 导入相关库


In [3]:
import jieba
import jieba.posseg as pseg
import nltk
import spacy
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from pathlib import Path

### 0.3 设置相关参数

PATH_MAPPING —— 文件路径


In [4]:
# 路径设置
PATH_MAPPING = {
    "DATASETS": Path("datasets"),
    "OUTPUTS": Path("outputs")
}

# 1. 数据预处理


## 1.1 设置文件数据架构和预处理函数


In [5]:
from dataclasses import dataclass

nlp = spacy.load("zh_core_web_sm")
@dataclass
class DataStruct:
    name : str
    path : Path
    textlist : list[str]

    def preprocessing(self):
        if self.textlist:
            for sentence in self.textlist:
                #sentence = str.join("", self.textlist)
                # 分词
                words = jieba.cut(sentence)
                print("分词结果:", list(words))
                # 词性标注
                words_with_pos = pseg.cut(sentence)
                print("词性标注结果:", [(word, flag) for word, flag in words_with_pos])
                # 命名实体识别
                doc = nlp(sentence)
                print("命名实体识别结果:", [(ent.text, ent.label_) for ent in doc.ents])
                # 去除停用词（以一个简单的停用词列表为例）
                stopwords = set(["的", "了", "在"])
                filtered_words = [word for word in jieba.cut(sentence) if word not in stopwords]
                #print("去除停用词结果:", filtered_words)
                # 向量化（使用spacy）
                vectorized_sentence = doc.vector
                print("向量化结果:", vectorized_sentence)
        else:
            print("数据不存在！")

# 1.2 读取文件


In [6]:
# 设置excel表格中的列名
COLUMNNAMES = ["评论内容", "博文内容"]
data_structs : list[DataStruct] = []
# 读取excel表格中的数据并整理为DataStruct
for file_path in list(PATH_MAPPING['DATASETS'].rglob('*.xlsx')):
    df = pd.read_excel(file_path, engine="openpyxl")
    for column in COLUMNNAMES:
        if column in df.columns:
            data_structs.append(DataStruct(name=(f"[{column}]{file_path.name}"), path=file_path, textlist=list(df[column])))
# 读取txt中的数据并整理为DataStruct
for file_path in list(PATH_MAPPING['DATASETS'].rglob('*.txt')):
    with open(file_path, 'r', encoding='utf8') as f:
        data_structs.append(DataStruct(name=f"[评论内容]{file_path.name}", path=file_path, textlist=f.readlines()))
# 统计数据
print("共生成", len(data_structs), "条数据结构.") 
for data in data_structs:
    print(" -", data.name, ": 共计", len(data.textlist) ,"条数据.")

共生成 6 条数据结构.
 - [博文内容]博文筛选后.xlsx : 共计 2457 条数据.
 - [评论内容]博文评论0721.xlsx : 共计 68979 条数据.
 - [评论内容]合并.txt : 共计 3200 条数据.
 - [评论内容]淮安河下古镇.txt : 共计 704 条数据.
 - [评论内容]淮安花街.txt : 共计 1154 条数据.
 - [评论内容]淮安里运河文化长廊.txt : 共计 1342 条数据.


In [7]:
data_structs[0].preprocessing()

Building prefix dict from the default dictionary ...
Loading model from cache C:\Users\Sparr\AppData\Local\Temp\jieba.cache
Loading model cost 0.406 seconds.
Prefix dict has been built successfully.


分词结果: ['【', '#', '6', '岁', '萌娃', '春节', '游船', '上', '弹', '古筝', '#', ' ', '余音袅袅', '画面', '唯美', '】', '2', '月', '16', '日', '，', '江苏', '淮安', '里运河', '文化', '长廊', '景区', '，', '6', '岁', '的', '璟', '瑢', '和', '小伙伴', '们', '在', '游船', '上', '表演', '古筝', '。', '一位', '市民', '称', '，', '小朋友', '们', '能', '在', '这么', '多人', '面前', '大方', '地', '展现', '自己', '，', '非常', '棒', '。', '景区', '工作人员', '说', '，', '这么', '冷', '的', '天气', '，', '小朋友', '们', '能', '如期', '到来', '，', '并且', '不折不扣', '地', '完成', '表演', '，', '非常', '值得', '大家', '点赞', '。', ' ', 'http', ':', '/', '/', 't', '.', 'cn', '/', 'A6ttU7YD']
词性标注结果: [('【', 'x'), ('#', 'x'), ('6', 'm'), ('岁', 'm'), ('萌', 'v'), ('娃', 'ng'), ('春节', 't'), ('游船', 'n'), ('上', 'f'), ('弹', 'v'), ('古筝', 'n'), ('#', 'x'), (' ', 'x'), ('余音袅袅', 'l'), ('画面', 'n'), ('唯美', 'a'), ('】', 'x'), ('2', 'm'), ('月', 'm'), ('16', 'm'), ('日', 'm'), ('，', 'x'), ('江苏', 'ns'), ('淮安', 'ns'), ('里运河', 'ns'), ('文化', 'n'), ('长廊', 'n'), ('景区', 'n'), ('，', 'x'), ('6', 'm'), ('岁', 'm'), ('的', 'uj'), ('璟', 'y'), ('瑢', 'y'), ('和', 